In [1]:
# import required packages 
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, mean_squared_error
import seaborn as sns

from sklearn import preprocessing,model_selection,neighbors,svm
from sklearn.preprocessing import StandardScaler, RobustScaler, MaxAbsScaler, MinMaxScaler
from sklearn.metrics import accuracy_score, mean_squared_error, mean_absolute_error

from catboost import CatBoostClassifier,CatBoostRegressor,cv,Pool
from tqdm import tqdm as tqdm

import warnings
warnings.filterwarnings('ignore')

### What will we do in this notebook?

In this notebod we will use a dataset based on real market data to predict the daily autogas sales in Turkey.
Our data is approxitely for 1.5 years (from June 2020 to Jan 2022).  

# 1. Read & Manipulate Data

In [6]:
# read data file
path = "input v3.xlsx"
data=pd.read_excel(path,sheet_name="data")
data.tail()

Date  Wholesale  Cylindrical Sale  Bulk Sale  Autogas Sale  \
596 2022-01-18          0                 0          0             0   
597 2022-01-19          0                 0          0             0   
598 2022-01-20          0                 0          0             0   
599 2022-01-21          0                 0          0             0   
600 2022-01-22          0                 0          0             0   

     Total Sale  Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  \
596           0    0.0                          0.0                  12135.18   
597           0    0.0                          0.0                  12135.18   
598           0    0.0                          0.0                  12135.18   
599           0    0.0                          0.0                  12135.18   
600           0    0.0                          0.0                  12135.18   

     Year  Month  Day  Weekday Special_Day_Type_Holiday  \
596  2022      1   18        3                        0   
597  2022      1   19        4                        0   
598  2022      1   20        5                        0   
599  2022      1   21        6                        0   
600  2022      1   22        7                        0   

    Special_Day_Type_Month Special_Day_Type_Raise Special_Day_Type_Discount  \
596                      0                      0                         0   
597                      0                      0                         0   
598                      0                      0                         0   
599                      0                      0                         0   
600                      0                      0                         0   

     Covid Cases  Covid Deaths  Death/recovering  
596            0           173           0.00492  
597            0           173           0.00492  
598            0           173           0.00492  
599            0           173           0.00492  
600            0           173           0.00492

When we look at the data we do not see any NaN value in each column

In [7]:
data.isnull().any()

Date                           False
Wholesale                      False
Cylindrical Sale               False
Bulk Sale                      False
Autogas Sale                   False
Total Sale                     False
Limit                          False
TUPRAS Price Change  TL/ton    False
TUPRAS Price (OTV+Gelir)       False
Year                           False
Month                          False
Day                            False
Weekday                        False
Special_Day_Type_Holiday       False
Special_Day_Type_Month         False
Special_Day_Type_Raise         False
Special_Day_Type_Discount      False
Covid Cases                    False
Covid Deaths                   False
Death/recovering               False
dtype: bool

In [4]:
print(" the data contains : {} rows and {} columns".format(data.shape[0],data.shape[1]))

 the data contains : 600 rows and 20 columns


In [117]:
# Set the Date column as index 
data.set_index("Date",inplace=True)

In [4]:
data.describe()

Wholesale  Cylindrical Sale      Bulk Sale  Autogas Sale  \
count  6.000000e+02      6.000000e+02     600.000000  6.000000e+02   
mean   9.254815e+05      3.517325e+05   11155.493333  4.605386e+05   
std    7.127715e+05      2.065618e+05   22204.234569  1.576148e+05   
min    0.000000e+00      0.000000e+00       0.000000  0.000000e+00   
25%    4.480750e+05      2.530058e+05    2874.500000  3.833652e+05   
50%    8.043900e+05      3.915635e+05    7268.500000  4.733740e+05   
75%    1.224600e+06      4.692910e+05   12548.500000  5.593192e+05   
max    9.165980e+06      1.122743e+06  284016.000000  1.102172e+06   

         Total Sale       Limit  TUPRAS Price Change  TL/ton  \
count  6.000000e+02  600.000000                   600.000000   
mean   2.014402e+06    0.001828                    14.450217   
std    1.246768e+06    0.011437                   169.022442   
min    0.000000e+00   -0.069987                 -2861.644100   
25%    1.328368e+06    0.000000                     0.000000   
50%    1.670503e+06    0.000000                     0.000000   
75%    2.393966e+06    0.000000                     0.000000   
max    1.187850e+07    0.111272                  1174.656150   

       TUPRAS Price (OTV+Gelir)         Year       Month         Day  \
count                600.000000   600.000000  600.000000  600.000000   
mean                5592.743941  2020.678333    7.216667   15.580000   
std                 2112.428430     0.537288    3.385088    8.776977   
min                 3461.610000  2020.000000    1.000000    1.000000   
25%                 4466.280000  2020.000000    5.000000    8.000000   
50%                 4467.336150  2021.000000    8.000000   15.500000   
75%                 5852.940000  2021.000000   10.000000   23.000000   
max                12135.180000  2022.000000   12.000000   31.000000   

          Weekday  Covid Cases  Covid Deaths  Death/recovering  
count  600.000000   600.000000    600.000000        600.000000  
mean     4.000000  1153.938333    135.396667          0.017658  
std      1.997494  1426.639255     88.411464          0.014480  
min      1.000000     0.000000     14.000000          0.003964  
25%      2.000000     0.000000     59.000000          0.007780  
50%      4.000000   830.500000    131.500000          0.011947  
75%      6.000000  1529.750000    203.000000          0.019331  
max      7.000000  7381.000000    394.000000          0.070107

In [5]:
data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 600 entries, 2020-06-01 to 2022-01-21
Data columns (total 19 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   Wholesale                    600 non-null    int64  
 1   Cylindrical Sale             600 non-null    int64  
 2   Bulk Sale                    600 non-null    int64  
 3   Autogas Sale                 600 non-null    int64  
 4   Total Sale                   600 non-null    int64  
 5   Limit                        600 non-null    float64
 6   TUPRAS Price Change  TL/ton  600 non-null    float64
 7   TUPRAS Price (OTV+Gelir)     600 non-null    float64
 8   Year                         600 non-null    int64  
 9   Month                        600 non-null    int64  
 10  Day                          600 non-null    int64  
 11  Weekday                      600 non-null    int64  
 12  Special_Day_Type_Holiday     600 non-null    object 
 13  S

In [8]:
data.columns

Index(['Date', 'Wholesale', 'Cylindrical Sale', 'Bulk Sale', 'Autogas Sale',
       'Total Sale', 'Limit', 'TUPRAS Price Change  TL/ton',
       'TUPRAS Price (OTV+Gelir)', 'Year', 'Month', 'Day', 'Weekday',
       'Special_Day_Type_Holiday', 'Special_Day_Type_Month',
       'Special_Day_Type_Raise', 'Special_Day_Type_Discount', 'Covid Cases',
       'Covid Deaths', 'Death/recovering'],
      dtype='object')

In [9]:
data[['Wholesale', 'Cylindrical Sale', 'Bulk Sale', 'Autogas Sale','Total Sale']] = data[['Wholesale', 'Cylindrical Sale', 'Bulk Sale', 'Autogas Sale','Total Sale']]/1000

## 1.1 Add new features 

In [10]:
data["Autogas-7"] = data["Autogas Sale"].shift(7)
data["Wholesale-7"] = data["Wholesale"].shift(7)
data["Cylindrical-7"] = data["Cylindrical Sale"].shift(7)
data["Bulk-7"] = data["Bulk Sale"].shift(7)
data["Total-7"] = data["Total Sale"].shift(7)

In [6]:
# Define new features 
# We think that demand in each sub category related to the previous day and previous week sales
# we create new columns for each sale category for previous daya and previous week  


data["Autogas-7"] = data["Autogas Sale"].shift(7)
data["Wholesale-7"] = data["Wholesale"].shift(7)
data["Cylindrical-7"] = data["Cylindrical Sale"].shift(7)
data["Bulk-7"] = data["Bulk Sale"].shift(7)
data["Total-7"] = data["Total Sale"].shift(7)



data["Autogas-1"] = data["Autogas Sale"].shift(1)
data["Wholesale-1"] = data["Wholesale"].shift(1)
data["Cylindrical-1"] = data["Cylindrical Sale"].shift(1)
data["Bulk-1"] = data["Bulk Sale"].shift(1)
data["Total-1"] = data["Total Sale"].shift(1)


In [11]:
data.dropna(inplace=True)

In [13]:
data.tail()

Date  Wholesale  Cylindrical Sale  Bulk Sale  Autogas Sale  \
596 2022-01-18        0.0               0.0        0.0           0.0   
597 2022-01-19        0.0               0.0        0.0           0.0   
598 2022-01-20        0.0               0.0        0.0           0.0   
599 2022-01-21        0.0               0.0        0.0           0.0   
600 2022-01-22        0.0               0.0        0.0           0.0   

     Total Sale  Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  \
596         0.0    0.0                          0.0                  12135.18   
597         0.0    0.0                          0.0                  12135.18   
598         0.0    0.0                          0.0                  12135.18   
599         0.0    0.0                          0.0                  12135.18   
600         0.0    0.0                          0.0                  12135.18   

     Year  ...  Special_Day_Type_Raise  Special_Day_Type_Discount  \
596  2022  ...                       0                          0   
597  2022  ...                       0                          0   
598  2022  ...                       0                          0   
599  2022  ...                       0                          0   
600  2022  ...                       0                          0   

     Covid Cases Covid Deaths Death/recovering Autogas-7 Wholesale-7  \
596            0          173          0.00492   496.066      856.44   
597            0          173          0.00492   123.632      686.02   
598            0          173          0.00492   168.102      592.12   
599            0          173          0.00492   357.755      756.08   
600            0          173          0.00492   339.958     1062.00   

     Cylindrical-7  Bulk-7   Total-7  
596        499.957   7.510  1859.973  
597        733.539   3.801  7048.142  
598        110.981  18.066   889.269  
599        166.869  16.786  2998.954  
600         80.802   0.918  1483.678  

[5 rows x 25 columns]

In [9]:
data.tail()

Wholesale  Cylindrical Sale  Bulk Sale  Autogas Sale  Total Sale  \
Date                                                                           
2022-01-17          0                 0          0             0           0   
2022-01-18          0                 0          0             0           0   
2022-01-19          0                 0          0             0           0   
2022-01-20          0                 0          0             0           0   
2022-01-21          0                 0          0             0           0   

            Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  \
Date                                                                       
2022-01-17    0.0                          0.0                  12135.18   
2022-01-18    0.0                          0.0                  12135.18   
2022-01-19    0.0                          0.0                  12135.18   
2022-01-20    0.0                          0.0                  12135.18   
2022-01-21    0.0                          0.0                  12135.18   

            Year  Month  ...  Autogas-7  Wholesale-7 Cylindrical-7   Bulk-7  \
Date                     ...                                                  
2022-01-17  2022      1  ...   644886.0    1264300.0      527552.0   7835.0   
2022-01-18  2022      1  ...   496066.0     856440.0      499957.0   7510.0   
2022-01-19  2022      1  ...   123632.0     686020.0      733539.0   3801.0   
2022-01-20  2022      1  ...   168102.0     592120.0      110981.0  18066.0   
2022-01-21  2022      1  ...   357755.0     756080.0      166869.0  16786.0   

              Total-7 Autogas-1  Wholesale-1  Cylindrical-1  Bulk-1   Total-1  
Date                                                                           
2022-01-17  2444573.0  227346.0     617640.0            0.0  4250.0  849236.0  
2022-01-18  1859973.0       0.0          0.0            0.0     0.0       0.0  
2022-01-19  7048142.0       0.0          0.0            0.0     0.0       0.0  
2022-01-20   889269.0       0.0          0.0            0.0     0.0       0.0  
2022-01-21  2998954.0       0.0          0.0            0.0     0.0       0.0  

[5 rows x 29 columns]

In [10]:
data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 593 entries, 2020-06-08 to 2022-01-21
Data columns (total 29 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   Wholesale                    593 non-null    int64  
 1   Cylindrical Sale             593 non-null    int64  
 2   Bulk Sale                    593 non-null    int64  
 3   Autogas Sale                 593 non-null    int64  
 4   Total Sale                   593 non-null    int64  
 5   Limit                        593 non-null    float64
 6   TUPRAS Price Change  TL/ton  593 non-null    float64
 7   TUPRAS Price (OTV+Gelir)     593 non-null    float64
 8   Year                         593 non-null    int64  
 9   Month                        593 non-null    int64  
 10  Day                          593 non-null    int64  
 11  Weekday                      593 non-null    int64  
 12  Special_Day_Type_Holiday     593 non-null    object 
 13  S

## 1.2 Categorization of data as categorical and numerical 

In [14]:

X = data.drop(columns=["Wholesale","Cylindrical Sale","Bulk Sale","Autogas Sale","Total Sale"], axis=1)
X.head()

Date  Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  \
7  2020-06-08    0.0                          0.0                   3752.43   
8  2020-06-09    0.0                          0.0                   3752.43   
9  2020-06-10    0.0                          0.0                   3752.43   
10 2020-06-11    0.0                          0.0                   3752.43   
11 2020-06-12    0.0                          0.0                   3752.43   

    Year  Month  Day  Weekday Special_Day_Type_Holiday Special_Day_Type_Month  \
7   2020      6    8        2                        0                      0   
8   2020      6    9        3                        0                      0   
9   2020      6   10        4                        0                      0   
10  2020      6   11        5                        0                      0   
11  2020      6   12        6                        0                      0   

   Special_Day_Type_Raise Special_Day_Type_Discount  Covid Cases  \
7                       0                         0          989   
8                       0                         0          993   
9                       0                         0          922   
10                      0                         0          987   
11                      0                         0         1195   

    Covid Deaths  Death/recovering  Autogas-7  Wholesale-7  Cylindrical-7  \
7             19          0.005570    171.280       216.80        729.273   
8             18          0.005594    657.056       336.38        712.024   
9             17          0.007586    375.137       202.42        187.235   
10            17          0.016650    422.513       244.14        303.234   
11            15          0.012077    578.255       367.68        288.031   

    Bulk-7   Total-7  
7    5.961  1123.314  
8    7.134  1712.594  
9   10.074   774.866  
10   3.724   973.611  
11   2.225  1236.191

In [15]:
X.tail()

Date  Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  \
596 2022-01-18    0.0                          0.0                  12135.18   
597 2022-01-19    0.0                          0.0                  12135.18   
598 2022-01-20    0.0                          0.0                  12135.18   
599 2022-01-21    0.0                          0.0                  12135.18   
600 2022-01-22    0.0                          0.0                  12135.18   

     Year  Month  Day  Weekday Special_Day_Type_Holiday  \
596  2022      1   18        3                        0   
597  2022      1   19        4                        0   
598  2022      1   20        5                        0   
599  2022      1   21        6                        0   
600  2022      1   22        7                        0   

    Special_Day_Type_Month Special_Day_Type_Raise Special_Day_Type_Discount  \
596                      0                      0                         0   
597                      0                      0                         0   
598                      0                      0                         0   
599                      0                      0                         0   
600                      0                      0                         0   

     Covid Cases  Covid Deaths  Death/recovering  Autogas-7  Wholesale-7  \
596            0           173           0.00492    496.066       856.44   
597            0           173           0.00492    123.632       686.02   
598            0           173           0.00492    168.102       592.12   
599            0           173           0.00492    357.755       756.08   
600            0           173           0.00492    339.958      1062.00   

     Cylindrical-7  Bulk-7   Total-7  
596        499.957   7.510  1859.973  
597        733.539   3.801  7048.142  
598        110.981  18.066   889.269  
599        166.869  16.786  2998.954  
600         80.802   0.918  1483.678

In [16]:
X_num = X._get_numeric_data()
X_cat = X.select_dtypes(include=["object"])

In [17]:
X_cat.head()

Special_Day_Type_Holiday Special_Day_Type_Month Special_Day_Type_Raise  \
7                         0                      0                      0   
8                         0                      0                      0   
9                         0                      0                      0   
10                        0                      0                      0   
11                        0                      0                      0   

   Special_Day_Type_Discount  
7                          0  
8                          0  
9                          0  
10                         0  
11                         0

In [18]:
X_num.head()

Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  Year  Month  \
7     0.0                          0.0                   3752.43  2020      6   
8     0.0                          0.0                   3752.43  2020      6   
9     0.0                          0.0                   3752.43  2020      6   
10    0.0                          0.0                   3752.43  2020      6   
11    0.0                          0.0                   3752.43  2020      6   

    Day  Weekday  Covid Cases  Covid Deaths  Death/recovering  Autogas-7  \
7     8        2          989            19          0.005570    171.280   
8     9        3          993            18          0.005594    657.056   
9    10        4          922            17          0.007586    375.137   
10   11        5          987            17          0.016650    422.513   
11   12        6         1195            15          0.012077    578.255   

    Wholesale-7  Cylindrical-7  Bulk-7   Total-7  
7        216.80        729.273   5.961  1123.314  
8        336.38        712.024   7.134  1712.594  
9        202.42        187.235  10.074   774.866  
10       244.14        303.234   3.724   973.611  
11       367.68        288.031   2.225  1236.191

In [19]:
# by using get_dummies function label enncode the categorical features
X_cat_copy= X_cat.copy()
for col in X_cat.columns:
    X_cat_col=pd.get_dummies(X_cat[col],prefix=col,prefix_sep="_",dummy_na=False,drop_first=True)
    X_cat = pd.concat([X_cat.drop(col,axis=1),X_cat_col],axis=1)

In [20]:
X_cat.shape

(594, 32)

In [21]:
X_cat.tail()

Special_Day_Type_Holiday_KB+1  Special_Day_Type_Holiday_KB+2  \
596                              0                              0   
597                              0                              0   
598                              0                              0   
599                              0                              0   
600                              0                              0   

     Special_Day_Type_Holiday_KB1  Special_Day_Type_Holiday_KB2  \
596                             0                             0   
597                             0                             0   
598                             0                             0   
599                             0                             0   
600                             0                             0   

     Special_Day_Type_Holiday_KB3  Special_Day_Type_Holiday_KB4  \
596                             0                             0   
597                             0                             0   
598                             0                             0   
599                             0                             0   
600                             0                             0   

     Special_Day_Type_Holiday_KBA  Special_Day_Type_Holiday_KBA-1  \
596                             0                               0   
597                             0                               0   
598                             0                               0   
599                             0                               0   
600                             0                               0   

     Special_Day_Type_Holiday_KBA-2  Special_Day_Type_Holiday_RB+1  ...  \
596                               0                              0  ...   
597                               0                              0  ...   
598                               0                              0  ...   
599                               0                              0  ...   
600                               0                              0  ...   

     Special_Day_Type_Month_A-1  Special_Day_Type_Month_A0  \
596                           0                          0   
597                           0                          0   
598                           0                          0   
599                           0                          0   
600                           0                          0   

     Special_Day_Type_Raise_Z  Special_Day_Type_Raise_Z+1  \
596                         0                           0   
597                         0                           0   
598                         0                           0   
599                         0                           0   
600                         0                           0   

     Special_Day_Type_Raise_Z-1  Special_Day_Type_Raise_Z-2  \
596                           0                           0   
597                           0                           0   
598                           0                           0   
599                           0                           0   
600                           0                           0   

     Special_Day_Type_Discount_I  Special_Day_Type_Discount_I+1  \
596                            0                              0   
597                            0                              0   
598                            0                              0   
599                            0                              0   
600                            0                              0   

     Special_Day_Type_Discount_I-1  Special_Day_Type_Discount_I-2  
596                              0                              0  
597                              0                              0  
598                              0                              0  
599                              0                              0  
600                              0                      

In [22]:
# concatenate the numerical and categorical features
# now our data is ready to deploy
X = pd.concat([X_num,X_cat],axis=1)
y = data['Autogas Sale']

We would like to find the best model predicting the Autogas Sales

In [20]:
y.shape

(593,)

In [21]:
y.head()

Date
2020-06-08    533995
2020-06-09    515611
2020-06-10    575367
2020-06-11    538706
2020-06-12    604258
Name: Autogas Sale, dtype: int64

In [22]:
X_num.tail()

Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  \
Date                                                                       
2022-01-17    0.0                          0.0                  12135.18   
2022-01-18    0.0                          0.0                  12135.18   
2022-01-19    0.0                          0.0                  12135.18   
2022-01-20    0.0                          0.0                  12135.18   
2022-01-21    0.0                          0.0                  12135.18   

            Year  Month  Day  Weekday  Covid Cases  Covid Deaths  \
Date                                                               
2022-01-17  2022      1   17        2            0           173   
2022-01-18  2022      1   18        3            0           173   
2022-01-19  2022      1   19        4            0           173   
2022-01-20  2022      1   20        5            0           173   
2022-01-21  2022      1   21        6            0           173   

            Death/recovering  Autogas-7  Wholesale-7  Cylindrical-7   Bulk-7  \
Date                                                                           
2022-01-17           0.00492   644886.0    1264300.0       527552.0   7835.0   
2022-01-18           0.00492   496066.0     856440.0       499957.0   7510.0   
2022-01-19           0.00492   123632.0     686020.0       733539.0   3801.0   
2022-01-20           0.00492   168102.0     592120.0       110981.0  18066.0   
2022-01-21           0.00492   357755.0     756080.0       166869.0  16786.0   

              Total-7  Autogas-1  Wholesale-1  Cylindrical-1  Bulk-1   Total-1  
Date                                                                            
2022-01-17  2444573.0   227346.0     617640.0            0.0  4250.0  849236.0  
2022-01-18  1859973.0        0.0          0.0            0.0     0.0       0.0  
2022-01-19  7048142.0        0.0          0.0            0.0     0.0       0.0  
2022-01-20   889269.0        0.0          0.0            0.0     0.0       0.0  
2022-01-21  2998954.0        0.0          0.0            0.0     0.0       0.0

# 2. Machine Learining Models & Implementations

In this past we will look at different ML models to meausre the performance of each and find the best model by looking at the performance metrics such as R2, MSE and MAE

## 2.1 Catboost

### 2.1.1 Scaling

In [24]:
# Our data set has a lot of numeric data and some features are numericall really big,
#  we need to scale our data to get a better understanding for the model.


scaler=MinMaxScaler()
scaler.fit(X)
X_scaled = pd.DataFrame(scaler.transform(X), columns=X.columns)
X_scaled.index=X.index
X_scaled.tail(8)

Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  Year  \
593  0.386114                     0.708977                       1.0   1.0   
594  0.386114                     0.708977                       1.0   1.0   
595  0.386114                     0.708977                       1.0   1.0   
596  0.386114                     0.708977                       1.0   1.0   
597  0.386114                     0.708977                       1.0   1.0   
598  0.386114                     0.708977                       1.0   1.0   
599  0.386114                     0.708977                       1.0   1.0   
600  0.386114                     0.708977                       1.0   1.0   

     Month       Day   Weekday  Covid Cases  Covid Deaths  Death/recovering  \
593    0.0  0.466667  1.000000          0.0      0.418421          0.014453   
594    0.0  0.500000  0.000000          0.0      0.418421          0.014453   
595    0.0  0.533333  0.166667          0.0      0.418421          0.014453   
596    0.0  0.566667  0.333333          0.0      0.418421          0.014453   
597    0.0  0.600000  0.500000          0.0      0.418421          0.014453   
598    0.0  0.633333  0.666667          0.0      0.418421          0.014453   
599    0.0  0.666667  0.833333          0.0      0.418421          0.014453   
600    0.0  0.700000  1.000000          0.0      0.418421          0.014453   

     ...  Special_Day_Type_Month_A-1  Special_Day_Type_Month_A0  \
593  ...                         0.0                        0.0   
594  ...                         0.0                        0.0   
595  ...                         0.0                        0.0   
596  ...                         0.0                        0.0   
597  ...                         0.0                        0.0   
598  ...                         0.0                        0.0   
599  ...                         0.0                        0.0   
600  ...                         0.0                        0.0   

     Special_Day_Type_Raise_Z  Special_Day_Type_Raise_Z+1  \
593                       0.0                         0.0   
594                       0.0                         0.0   
595                       0.0                         0.0   
596                       0.0                         0.0   
597                       0.0                         0.0   
598                       0.0                         0.0   
599                       0.0                         0.0   
600                       0.0                         0.0   

     Special_Day_Type_Raise_Z-1  Special_Day_Type_Raise_Z-2  \
593                         0.0                         0.0   
594                         0.0                         0.0   
595                         0.0                         0.0   
596                         0.0                         0.0   
597                         0.0                         0.0   
598                         0.0                         0.0   
599                         0.0                         0.0   
600                         0.0                         0.0   

     Special_Day_Type_Discount_I  Special_Day_Type_Discount_I+1  \
593                          0.0                            0.0   
594                          0.0                            0.0   
595                          0.0                            0.0   
596                          0.0                            0.0   
597                          0.0                            0.0   
598                          0.0                            0.0   
599                          0.0                            0.0   
600                          0.0                            0.0   

     Special_Day_Type_Discount_I-1  Special_Day_Type_Discount_I-2  
593                            0.0                            0.0  
594                            0.0                            0.0  
595                            0.0                            0

### 2.1.2 Train& Test split

In [25]:

X_train, X_test, y_train, y_test = model_selection.train_test_split(X_scaled, y, test_size=0.1, shuffle = True,random_state=42)
#X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.2, shuffle = True)
X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.1, shuffle = False)
print("Train", X_train.shape, y_train.shape)
print("Valid", X_valid.shape, y_valid.shape)
print("Test", X_test.shape, y_test.shape)

Train (480, 47) (480,)
Valid (54, 47) (54,)
Test (60, 47) (60,)


### 2.1.3 Model

In [26]:
model = CatBoostRegressor(iterations=20_000,
                          verbose=200, 
                          boosting_type = 'Ordered',
                          early_stopping_rounds=200,
                          loss_function = 'RMSE',
                          custom_metric = 'MAE',
                          task_type = 'CPU'
                          )

model.fit(X_train, y_train, eval_set=(X_valid, y_valid), use_best_model = True)

Learning rate set to 0.007298
0:	learn: 159.4253089	test: 108.6049633	best: 108.6049633 (0)	total: 176ms	remaining: 58m 29s
200:	learn: 103.7575456	test: 90.6029884	best: 90.4723840 (190)	total: 2.8s	remaining: 4m 35s
Stopped by overfitting detector  (200 iterations wait)

bestTest = 90.47238403
bestIteration = 190

Shrink model to first 191 iterations.


In [27]:
y_pred = model.predict(X_valid)
print("mean absolute error validation: ", mean_absolute_error(y_valid, y_pred) )

y_pred= model.predict(X_test)
print("mean absolute error test: ", mean_absolute_error(y_test, y_pred) )


y_pred= model.predict(X_test)
print("r2 score: ", r2_score(y_test, y_pred) )

mean absolute error validation:  66.56393120128729
mean absolute error test:  91.6285388297694
r2 score:  0.44290987362209233


In [28]:
model.predict(X[-5:])

array([461.74230718, 461.74230718, 461.74230718, 461.74230718,
       461.74230718])

### 2.1.4 Hyper Parameter Tuning

In [30]:
                          
grid_catboost = {
    'boosting_type': ['Ordered', 'Plain'],
    'learning_rate': [0.003, 0.006, 0.009, 0.03, 0.1, 0.5,1],
    'depth': [4, 6, 10,15,20],
    'l2_leaf_reg': [1, 3, 5, 7, 9,13]
}

In [31]:

def find_optimal_catboost_model(X, y, grid, is_scaled=False, test_size = .10, random_state=42, plot=True):
    '''
    finds the best CatBoost model parameters in the grid 
    INPUT
    X - pandas dataframe, X matrix
    y - pandas dataframe, response variable
    grid - python dictionary, set of all possible paramers 
    is_scaled- boolean, defaulst is Fale, True to scale the features set by using Standard Scaler
    test_size - float between 0 and 1, default 0.3, determines the proportion of data as test data
    random_state - int, default 42, controls random state for train_test_split
    plot - boolean, default 0.3, True to plot result

    OUTPUT
    r2_scores_test - list of floats of r2 scores on the test data
    r2_scores_train - list of floats of r2 scores on the train data
    catboost_model_tuned - CatBoostRegressor object which is the best model found by the optmimization of hypter parameters in the grid 
    X_train, X_test, y_train, y_test - output from sklearn train test split used for optimal model
    '''
    r2_scores_test, r2_scores_train, num_feats, results = [], [], [], dict()
    
    # if the given data is not scaled, scale it !
    if not is_scaled:
        scaler=MinMaxScaler()
        scaler.fit(X)
        X_scaled = pd.DataFrame(scaler.transform(X), columns=X.columns)
        X_scaled.index=X.index
        X = X_scaled.copy()

    X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=test_size,random_state=random_state, shuffle = True)
    #X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.2, shuffle = True)
    X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.1, shuffle = False)

    X_train_cv = pd.concat([X_train, X_valid])
    y_train_cv = pd.concat([y_train, y_valid])

    model_hyp = CatBoostRegressor(                          
                          early_stopping_rounds=200,
                          loss_function = 'RMSE',
                          custom_metric = 'MAE',
                          task_type = 'GPU'
                          )

    grid_search_results = model_hyp.grid_search(grid, X_train_cv, y_train_cv,verbose =200)

    catboost_model_tuned = CatBoostRegressor(**grid_search_results['params'])
    catboost_model_tuned.fit(X_train, y_train, eval_set=(X_valid, y_valid), use_best_model = True, plot=plot)
    y_test_preds=catboost_model_tuned.predict(X_test)
    r2_score_test = r2_score(y_test,y_test_preds)
    r2_score_train = r2_score(y_train,catboost_model_tuned.predict(X_train))

        
    return r2_score_test, r2_score_train, catboost_model_tuned, X_train, X_test, y_train, y_test

r2_test, r2_train, cb_tuned, X_train, X_test, y_train, y_test = find_optimal_catboost_model(X, y, grid_catboost)

0:	learn: 487.9550407	test: 476.1400485	best: 476.1400485 (0)	total: 29.4ms	remaining: 29.4s
1:	learn: 486.5866199	test: 474.8318148	best: 474.8318148 (1)	total: 49.4ms	remaining: 24.6s
2:	learn: 485.2183168	test: 473.5168285	best: 473.5168285 (2)	total: 70.5ms	remaining: 23.4s
3:	learn: 483.8687572	test: 472.1923416	best: 472.1923416 (3)	total: 90.4ms	remaining: 22.5s
4:	learn: 482.5439612	test: 470.8790943	best: 470.8790943 (4)	total: 108ms	remaining: 21.5s
5:	learn: 481.2073029	test: 469.6006058	best: 469.6006058 (5)	total: 127ms	remaining: 21s
6:	learn: 479.8620996	test: 468.3138575	best: 468.3138575 (6)	total: 147ms	remaining: 20.9s
7:	learn: 478.5291673	test: 467.0511789	best: 467.0511789 (7)	total: 170ms	remaining: 21s
8:	learn: 477.2447661	test: 465.7907958	best: 465.7907958 (8)	total: 192ms	remaining: 21.1s
9:	learn: 475.9593394	test: 464.5275361	best: 464.5275361 (9)	total: 209ms	remaining: 20.7s
10:	learn: 474.6394268	test: 463.2837688	best: 463.2837688 (10)	total: 231ms	rem

In [63]:
# Calculate R2 score
y_test_preds=cb_tuned.predict(X_test)
r2_score(y_test,y_test_preds)

0.7659332479859258

In [59]:
#Calculate mean squared error
mean_squared_error(y_test,y_test_preds)

5041053058.168069

In [60]:
# Calculate mean absolute error
mean_absolute_error(y_test,y_test_preds)

53016.45588458658

## 2.2 Gradient Boosting Method

In [43]:
# add related packages
import pandas as pd
import pickle
import numpy as np
from xlrd import open_workbook
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from scipy.stats import uniform, randint
from sklearn.model_selection import cross_val_score, GridSearchCV, KFold, RandomizedSearchCV, train_test_split
from sklearn.metrics import auc, accuracy_score, confusion_matrix, mean_squared_error
import warnings
from scipy.stats import uniform as sp_randFloat
from scipy.stats import randint as sp_randInt
from sklearn import ensemble
from sklearn import datasets
from sklearn.utils import shuffle
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from sklearn.datasets import load_digits
from sklearn.linear_model import SGDClassifier
from sklearn.ensemble import GradientBoostingRegressor
import xgboost 

### 2.2.1 Scaling

In [44]:
%%time

scaler=MinMaxScaler()
scaler.fit(X)
X_scaled = pd.DataFrame(scaler.transform(X), columns=X.columns)
X_scaled.index=X.index
X_scaled.tail(8)

Wall time: 8.94 ms


Limit  TUPRAS Price Change  TL/ton  TUPRAS Price (OTV+Gelir)  \
Date                                                                          
2022-01-14  0.386114                     0.708977                       1.0   
2022-01-15  0.386114                     0.708977                       1.0   
2022-01-16  0.386114                     0.708977                       1.0   
2022-01-17  0.386114                     0.708977                       1.0   
2022-01-18  0.386114                     0.708977                       1.0   
2022-01-19  0.386114                     0.708977                       1.0   
2022-01-20  0.386114                     0.708977                       1.0   
2022-01-21  0.386114                     0.708977                       1.0   

            Year  Month       Day   Weekday  Covid Cases  Covid Deaths  \
Date                                                                     
2022-01-14   1.0    0.0  0.433333  0.833333          0.0      0.418421   
2022-01-15   1.0    0.0  0.466667  1.000000          0.0      0.418421   
2022-01-16   1.0    0.0  0.500000  0.000000          0.0      0.418421   
2022-01-17   1.0    0.0  0.533333  0.166667          0.0      0.418421   
2022-01-18   1.0    0.0  0.566667  0.333333          0.0      0.418421   
2022-01-19   1.0    0.0  0.600000  0.500000          0.0      0.418421   
2022-01-20   1.0    0.0  0.633333  0.666667          0.0      0.418421   
2022-01-21   1.0    0.0  0.666667  0.833333          0.0      0.418421   

            Death/recovering  ...  Special_Day_Type_Month_A-1  \
Date                          ...                               
2022-01-14          0.014453  ...                         0.0   
2022-01-15          0.014453  ...                         0.0   
2022-01-16          0.014453  ...                         0.0   
2022-01-17          0.014453  ...                         0.0   
2022-01-18          0.014453  ...                         0.0   
2022-01-19          0.014453  ...                         0.0   
2022-01-20          0.014453  ...                         0.0   
2022-01-21          0.014453  ...                         0.0   

            Special_Day_Type_Month_A0  Special_Day_Type_Raise_Z  \
Date                                                              
2022-01-14                        0.0                       0.0   
2022-01-15                        0.0                       0.0   
2022-01-16                        0.0                       0.0   
2022-01-17                        0.0                       0.0   
2022-01-18                        0.0                       0.0   
2022-01-19                        0.0                       0.0   
2022-01-20                        0.0                       0.0   
2022-01-21                        0.0                       0.0   

            Special_Day_Type_Raise_Z+1  Special_Day_Type_Raise_Z-1  \
Date                                                                 
2022-01-14                         0.0                         0.0   
2022-01-15                         0.0                         0.0   
2022-01-16                         0.0                         0.0   
2022-01-17                         0.0                         0.0   
2022-01-18                         0.0                         0.0   
2022-01-19                         0.0                         0.0   
2022-01-20                         0.0                         0.0   
2022-01-21                         0.0                         0.0   

            Special_Day_Type_Raise_Z-2  Special_Day_Type_Discount_I  \
Date                                                                  
2022-01-14                         0.0                          0.0   
2022-01-15                         0.0                          0.0   
2022-01-16                         0.0                          0.0   
2022-01-17                         0.0                          0.0   
2022-01-18                        

### 2.2.2 Train & Test Split

In [45]:
X_train, X_test, y_train, y_test = train_test_split(X_scaled, y, test_size=0.1,shuffle=False) 

# {'learning_rate': 0.03, 'max_depth': 7, 'n_estimators': 374, 'subsample': 0.3800240596368538}

model = ensemble.GradientBoostingRegressor(learning_rate=0.1,
                          loss='ls', max_depth=3, max_features=None,
                          max_leaf_nodes=None, min_impurity_decrease=0.0,
                          min_samples_leaf=1,
                          min_weight_fraction_leaf=0.0,
                          n_iter_no_change=None,
                          random_state=None,
                          subsample=0.7269, tol=0.0001,
                          validation_fraction=0.1, verbose=0, warm_start=False)


model.fit(X_train , y_train)

GradientBoostingRegressor(loss='ls', subsample=0.7269)

In [46]:
y_test_preds=model.predict(X_test)
r2_score(y_test,y_test_preds)

0.061970817849166915

In [112]:
df = pd.concat([pd.Series(y_test.values),pd.Series(y_test_preds)], axis=1)
df.columns=["y_test","y_pred"]
df.index=y_test.index
df.head()

y_test      y_pred
Date                           
2021-11-14  522.167  336.143108
2021-11-15  845.767  622.695705
2021-11-16  182.904  326.701403
2021-11-17  315.818  410.017449
2021-11-18  398.077  437.994049

In [119]:
mean_absolute_error(y_test,y_test_preds)

### 2.2.2 Parameter Tuning 

In [114]:

# Define the grid of hyperparameters to search

parameters = {'learning_rate': [0.03, 0.1, 0.5,1],
              'subsample': sp_randFloat(),
              'max_depth': [3,4,5,6,7,8]
              }

gradientboost = GradientBoostingRegressor()

random_cv = RandomizedSearchCV(estimator=gradientboost,
                               param_distributions=parameters,
                               cv=5, n_iter=1500, n_jobs=-1)

random_cv.fit(X_train,Y_train)

print(random_cv.best_estimator_,1)
# Results from Random Search
print("\n========================================================")
print(" Results from Random Search ")
print("========================================================")

print("\n The best estimator across ALL searched params:\n",
      random_cv.best_estimator_)

print("\n The best score across ALL searched params:\n",
      random_cv.best_score_)

print("\n The best parameters across ALL searched params:\n",
      random_cv.best_params_)
print("\n ========================================================")


GradientBoostingRegressor(max_depth=5, subsample=0.7579834267839852) 1

 Results from Random Search 

 The best estimator across ALL searched params:
 GradientBoostingRegressor(max_depth=5, subsample=0.7579834267839852)

 The best score across ALL searched params:
 0.6571131114173074

 The best parameters across ALL searched params:
 {'learning_rate': 0.1, 'max_depth': 5, 'subsample': 0.7579834267839852}



In [51]:
# Define the grid of hyperparameters to search

gb_parameters = {'learning_rate': [0.03, 0.1, 0.5,1],
              'subsample': [0.6,0.7,0.8,0.9,1.0],
              'max_depth': [3,4,5,6,7,8]
              }

In [55]:
# Parameter tuning is done by Randomized Grid Search Method
def find_optimal_gb_model(X, y, parameters, is_scaled=False, test_size = .10, random_state=42, plot=True):
    '''
    finds the best CatBoost model parameters in the grid 
    INPUT
    X - pandas dataframe, X matrix
    y - pandas dataframe, response variable
    parameters - python dictionary, set of all possible Hyper parameters 
    is_scaled- boolean, defaulst is Fale, True to scale the features set by using Standard Scaler
    test_size - float between 0 and 1, default 0.3, determines the proportion of data as test data
    random_state - int, default 42, controls random state for train_test_split
    plot - boolean, default 0.3, True to plot result

    OUTPUT
    r2_scores_test - list of floats of r2 scores on the test data
    r2_scores_train - list of floats of r2 scores on the train data
    catboost_model_tuned - CatBoostRegressor object which is the best model found by the optmimization of hypter parameters in the grid 
    X_train, X_test, y_train, y_test - output from sklearn train test split used for optimal model
    '''
    r2_scores_test, r2_scores_train, num_feats, results = [], [], [], dict()
    
    # if the given data is not scaled, scale it !
    if not is_scaled:
        scaler=MinMaxScaler()
        scaler.fit(X)
        X_scaled = pd.DataFrame(scaler.transform(X), columns=X.columns)
        X_scaled.index=X.index
        X = X_scaled.copy()

    X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=test_size,random_state=random_state, shuffle = True)
    #X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.2, shuffle = True)
    X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.1, shuffle = False)

    X_train_cv = pd.concat([X_train, X_valid])
    y_train_cv = pd.concat([y_train, y_valid])

    gradientboost = GradientBoostingRegressor()

    random_cv = RandomizedSearchCV(estimator=gradientboost,
                                param_distributions=parameters,
                                cv=5, n_iter=1500, n_jobs=-1)

    random_cv.fit(X_train_cv,y_train_cv)
   
    # define the new Gradient Boost Regressor with the best hyper parameters combination by using Randomized Search Cross Validation Method
    gb_tuned = GradientBoostingRegressor(**random_cv.best_params_)
    gb_tuned.fit(X_train_cv,y_train_cv)

    y_test_preds=gb_tuned.predict(X_test)
    r2_score_test = r2_score(y_test,y_test_preds)
    r2_score_train = r2_score(y_train_cv,gb_tuned.predict(X_train_cv))

        
    return r2_score_test, r2_score_train, gb_tuned, X_train, X_test, y_train, y_test

r2_test, r2_train, gb_tuned, X_train, X_test, y_train, y_test = find_optimal_gb_model(X, y, gb_parameters)

In [58]:
r2_test

0.677667953002707

In [120]:
gb_tuned = GradientBoostingRegressor(**random_cv.best_params_)
gb_tuned.fit(X_train,y_train)

GradientBoostingRegressor(max_depth=5, subsample=0.7579834267839852)

In [59]:
y_pred = gb_tuned.predict(X_test)
r2_score(y_test,y_pred)

0.677667953002707

## 2.3 Random Forest 

In [60]:
from sklearn.ensemble import RandomForestRegressor
from pprint import pprint


### 2.3.1 Train Test Split

In [62]:
scaler=StandardScaler()
scaler.fit(X)
X_scaled = pd.DataFrame(scaler.transform(X), columns=X.columns)
X_scaled.index=X.index
X_train, X_test, y_train, y_test = train_test_split(X_scaled, y, test_size = .10, random_state=42) 


### 2.3.2 Model

In [132]:
rf = RandomForestRegressor(random_state = 42)
rf.fit(X_train,y_train)
y_pred = rf.precict(X_test)

In [ ]:
r2_score(y_test,y_pred)

# 2.3.2 Hyper Parameter Tuning

In [64]:
from sklearn.model_selection import RandomizedSearchCV
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(1, 20, num = 10)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4]
# Method of selecting samples for training each tree
bootstrap = [True, False]
# Create the random grid
rf_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}
pprint(rf_grid)

{'bootstrap': [True, False],
 'max_depth': [1, 3, 5, 7, 9, 11, 13, 15, 17, 20, None],
 'max_features': ['auto', 'sqrt'],
 'min_samples_leaf': [1, 2, 4],
 'min_samples_split': [2, 5, 10],
 'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000]}


In [137]:
# Use the random grid to search for best hyperparameters
# First create the base model to tune
rf = RandomForestRegressor()
# Random search of parameters, using 3 fold cross validation, 
# search across 100 different combinations, and use all available cores
rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 100, cv = 3, verbose=2, random_state=42, n_jobs = -1)
# Fit the random search model
rf_random.fit(X_train, y_train)

Fitting 3 folds for each of 100 candidates, totalling 300 fits


RandomizedSearchCV(cv=3, estimator=RandomForestRegressor(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [1, 3, 5, 7, 9, 11, 13, 15,
                                                      17, 20, None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4],
                                        'min_samples_split': [2, 5, 10],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=42, verbose=2)

In [73]:
# Parameter tuning is done by Randomized Grid Search Method
def find_optimal_rf_model(X, y, grid, is_scaled=False, test_size = 0.2, random_state=42, plot=True):
    '''
    finds the best CatBoost model parameters in the grid 
    INPUT
    X - pandas dataframe, X matrix
    y - pandas dataframe, response variable
    parameters - python dictionary, set of all possible Hyper parameters 
    is_scaled- boolean, defaulst is Fale, True to scale the features set by using Standard Scaler
    test_size - float between 0 and 1, default 0.3, determines the proportion of data as test data
    random_state - int, default 42, controls random state for train_test_split
    plot - boolean, default 0.3, True to plot result

    OUTPUT
    r2_scores_test - list of floats of r2 scores on the test data
    r2_scores_train - list of floats of r2 scores on the train data
    catboost_model_tuned - CatBoostRegressor object which is the best model found by the optmimization of hypter parameters in the grid 
    X_train, X_test, y_train, y_test - output from sklearn train test split used for optimal model
    '''
    r2_scores_test, r2_scores_train, num_feats, results = [], [], [], dict()
    
    # if the given data is not scaled, scale it !
    if not is_scaled:
        scaler=MinMaxScaler()
        scaler.fit(X)
        X_scaled = pd.DataFrame(scaler.transform(X), columns=X.columns)
        X_scaled.index=X.index
        X = X_scaled.copy()

    X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=test_size,random_state=random_state, shuffle = True)
    #X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.2, shuffle = True)
    X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.2, shuffle = False)

    X_train_cv = pd.concat([X_train, X_valid])
    y_train_cv = pd.concat([y_train, y_valid])

    # Use the random grid to search for best hyperparameters
    # First create the base model to tune
    rf = RandomForestRegressor()
    # Random search of parameters, using 3 fold cross validation, 
    # search across 100 different combinations, and use all available cores
    rf_random = RandomizedSearchCV(estimator = rf, param_distributions = grid, n_iter = 100, cv = 5, verbose=2, random_state=42, n_jobs = -1)
    # Fit the random search model
    rf_random.fit(X_train_cv, X_train_cv)
   
    # define the new Gradient Boost Regressor with the best hyper parameters combination by using Randomized Search Cross Validation Method
    rf_tuned = RandomForestRegressor(**rf_random.best_params_)
    rf_tuned.fit(X_train_cv,y_train_cv)

    y_test_preds=rf_tuned.predict(X_test)
    r2_score_test = r2_score(y_test,y_test_preds)
    r2_score_train = r2_score(y_train_cv,rf_tuned.predict(X_train_cv))

        
    return r2_score_test, r2_score_train, rf_tuned, X_train, X_test, y_train, y_test

r2_test, r2_train, rf_tuned, X_train, X_test, y_train, y_test = find_optimal_rf_model(X, y, rf_grid)

Fitting 5 folds for each of 100 candidates, totalling 500 fits


In [74]:
r2_test

0.6429215870079672

In [75]:
rf_tuned.get_params()

{'bootstrap': False,
 'ccp_alpha': 0.0,
 'criterion': 'squared_error',
 'max_depth': 17,
 'max_features': 'sqrt',
 'max_leaf_nodes': None,
 'max_samples': None,
 'min_impurity_decrease': 0.0,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'n_estimators': 400,
 'n_jobs': None,
 'oob_score': False,
 'random_state': None,
 'verbose': 0,
 'warm_start': False}

In [76]:
r2_score(y_test, rf_tuned.predict(X_test))

0.6429215870079672

In [77]:
rf_tuned.predict(X[-5:])

array([414214.912375, 235003.415   , 235003.415   , 235003.415   ,
       235003.415   ])

In [85]:
from sklearn.model_selection import GridSearchCV
# Create the parameter grid based on the results of random search 
param_grid = {
    'bootstrap': [True],
    'max_depth': [1,3,5,7,9,11,20,None],
    'max_features': [2, 3],
    'min_samples_leaf': [3, 4, 5],
    'min_samples_split': [8, 10, 12],
    'n_estimators': [100, 200, 300, 1000]
}
# Create a based model
rf = RandomForestRegressor()
# Instantiate the grid search model
grid_search = GridSearchCV(estimator = rf, param_grid = param_grid, 
                          cv = 4, n_jobs = -1, verbose = 2)

In [87]:
# Fit the grid search to the data
grid_search.fit(X_train, y_train)
grid_search.best_params_

Fitting 4 folds for each of 576 candidates, totalling 2304 fits


{'bootstrap': True,
 'max_depth': None,
 'max_features': 3,
 'min_samples_leaf': 3,
 'min_samples_split': 8,
 'n_estimators': 300}

In [88]:
rf_tuned = RandomForestRegressor(**grid_search.best_params_)
rf_tuned.fit(X_train, y_train)
r2_score(y_test, rf_tuned.predict(X_test))

0.4474615041424961

## 2.4 XGBOOST

In [90]:
#Importing Packages
import matplotlib.pyplot as plt

from xgboost import XGBRegressor
from xgboost import XGBRFRegressor
from sklearn.model_selection import GridSearchCV

from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error


In [91]:
print(xgboost.__version__)

1.5.0


### 2.4.1 Train Test Split and Model Data Preperation

In [92]:
scaler=StandardScaler()
scaler.fit(X)
X_scaled = pd.DataFrame(scaler.transform(X), columns=X.columns)
X_scaled.index=X.index

X_train, X_test, y_train, y_test = train_test_split(X_scaled, y, test_size = .20, random_state=42) 


In [93]:
import xgboost as xgb

dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test, label=y_test)

In [94]:
from sklearn.metrics import mean_absolute_error

In [95]:
#XGBoost hyper-parameter tuning
def hyperParameterTuning(X_train, y_train):
    param_tuning = {
        'learning_rate': [0.01, 0.1],
        'max_depth': [3, 5, 7, 10],
        'min_child_weight': [1, 3, 5],
        'subsample': [0.5, 0.7,0.9],
        'colsample_bytree': [0.5, 0.7],
        'n_estimators' : [100, 200, 500],
        'objective': ['reg:squarederror']
    }

    xgb_model = XGBRegressor()

    gsearch = GridSearchCV(estimator = xgb_model,
                           param_grid = param_tuning,                        
                           #scoring = 'neg_mean_absolute_error', #MAE
                           #scoring = 'neg_mean_squared_error',  #MSE
                           cv = 5,
                           n_jobs = -1,
                           verbose = 1)

    gsearch.fit(X_train,y_train)

    return gsearch.best_params_

hyperParameterTuning(X_train, y_train)  

Fitting 5 folds for each of 432 candidates, totalling 2160 fits


{'colsample_bytree': 0.5,
 'learning_rate': 0.01,
 'max_depth': 5,
 'min_child_weight': 1,
 'n_estimators': 500,
 'objective': 'reg:squarederror',
 'subsample': 0.7}

In [96]:
xgb_model = XGBRegressor(
        objective = 'reg:squarederror',
        colsample_bytree = 0.5,
        learning_rate = 0.01,
        max_depth = 5,
        min_child_weight = 1,
        n_estimators = 500,
        subsample = 0.7)

%time xgb_model.fit(X_train, y_train, early_stopping_rounds=20, eval_set=[(X_test, y_test)], verbose=False)

y_pred_xgb = xgb_model.predict(X_test)

mae_xgb = mean_absolute_error(y_test, y_pred_xgb)

print("MAE: ", mae_xgb)

Wall time: 753 ms
MAE:  69841.05245535714


In [97]:
r2_score(y_test, xgb_model.predict(X_test))

0.6670448472798838

### 2.4.2 Model and Hyper Parameter Tuning

In [101]:
xgb_grid = {
        'learning_rate': [0.01, 0.1],
        'max_depth': [3, 5, 7, 10],
        'min_child_weight': [1, 3, 5],
        'subsample': [0.5, 0.7,0.9],
        'colsample_bytree': [0.5, 0.7],
        'n_estimators' : [100, 200, 500],
        'objective': ['reg:squarederror']
    }



# Parameter tuning is done by Randomized Grid Search Method
def find_optimal_xgb_model(X, y, grid, is_scaled=False, test_size = 0.2, random_state=42, plot=True):
    '''
    finds the best CatBoost model parameters in the grid 
    INPUT
    X - pandas dataframe, X matrix
    y - pandas dataframe, response variable
    parameters - python dictionary, set of all possible Hyper parameters 
    is_scaled- boolean, defaulst is Fale, True to scale the features set by using Standard Scaler
    test_size - float between 0 and 1, default 0.3, determines the proportion of data as test data
    random_state - int, default 42, controls random state for train_test_split
    plot - boolean, default 0.3, True to plot result

    OUTPUT
    r2_scores_test - list of floats of r2 scores on the test data
    r2_scores_train - list of floats of r2 scores on the train data
    catboost_model_tuned - CatBoostRegressor object which is the best model found by the optmimization of hypter parameters in the grid 
    X_train, X_test, y_train, y_test - output from sklearn train test split used for optimal model
    '''
    r2_scores_test, r2_scores_train, num_feats, results = [], [], [], dict()
    
    # if the given data is not scaled, scale it !
    if not is_scaled:
        scaler=MinMaxScaler()
        scaler.fit(X)
        X_scaled = pd.DataFrame(scaler.transform(X), columns=X.columns)
        X_scaled.index=X.index
        X = X_scaled.copy()

    X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=test_size,random_state=random_state, shuffle = True)
    #X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.2, shuffle = True)
    X_train, X_valid, y_train, y_valid = model_selection.train_test_split(X_train, y_train, test_size=0.2, shuffle = False)

    X_train_cv = pd.concat([X_train, X_valid])
    y_train_cv = pd.concat([y_train, y_valid])

    xgb_model = XGBRegressor()

    gsearch = GridSearchCV(estimator = xgb_model,
                           param_grid = xgb_grid,                        
                           #scoring = 'neg_mean_absolute_error', #MAE
                           #scoring = 'neg_mean_squared_error',  #MSE
                           cv = 5,
                           n_jobs = -1,
                           verbose = 1)

    gsearch.fit(X_train_cv,y_train_cv)



    xgb_tuned = XGBRegressor(**gsearch.best_params_)

    xgb_tuned.fit(X_train, y_train, early_stopping_rounds=20, eval_set=[(X_test, y_test)], verbose=False)

    

    y_test_preds=xgb_tuned.predict(X_test)
    r2_score_test = r2_score(y_test,y_test_preds)
    r2_score_train = r2_score(y_train_cv,xgb_tuned.predict(X_train_cv))

        
    return r2_score_test, r2_score_train, xgb_tuned, X_train, X_test, y_train, y_test

r2_test, r2_train, xgb_tuned, X_train, X_test, y_train, y_test = find_optimal_xgb_model(X, y, xgb_grid)

Fitting 5 folds for each of 432 candidates, totalling 2160 fits


In [102]:
r2_test



0.6759107278604815

# 3. Results

We trained our data by using CatBoost, RandomForest, Gradient Boosting and  XGBoost models.
We did hypter parameyer tuning and by comparing the R2 scores we can say that CatBoostRegressor is the best model fitting our data set to precit the LPG Autogas Sale prices